In [1]:
# Clear workspace
%reset

# standard packages
from math import e
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import pickle as pkl
import os
from sklearn import preprocessing
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.metrics import classification_report, roc_curve, auc, roc_auc_score, precision_recall_curve, plot_precision_recall_curve
from scipy.stats import sem
pd.options.display.max_colwidth = 100

# SGL packages
from group_lasso import LogisticGroupLasso
LogisticGroupLasso.LOG_LOSSES = True

%reload_ext autoreload
%autoreload 2

working_dir = "~/Desktop/hif2gene"


Once deleted, variables cannot be recovered. Proceed (y/[n])? y


In [3]:
seed = 360
np.random.seed(seed)
outcome = 'PD1'

## Load in HIFs + Clusters 

In [4]:
# Load in HIF dataset with labels
# NAs removed, already converted to patient-level

df = pd.read_csv("{0}/data/genetic_data/PanImmune/datasets/pancancer.{1}.joined.USE.csv".format(working_dir, outcome))
df = df.iloc[:,1:]
df

AREA..MM2..OF..EPITHELIAL..IN..TISSUE._HE  \
0                                     71.806464   
1                                     82.396624   
2                                     26.877520   
3                                     43.128576   
4                                      0.685216   
...                                         ...   
1616                                  52.707784   
1617                                  63.597184   
1618                                  77.987908   
1619                                  39.603288   
1620                                  17.451352   

      AREA..MM2..OF..ESI_0080..IN..TISSUE._HE  \
0                                  129.127076   
1                                  168.316672   
2                                   53.040932   
3                                  111.292004   
4                                    2.596956   
...                                       ...   
1616                                98.824948   
1617                                70.101124   
1618                               106.847656   
1619                                65.279932   
1620                                20.754456   

      AREA..MM2..OF..NECROSIS..IN..TISSUE._HE  \
0                                    1.158576   
1                                    2.677280   
2                                    3.571664   
3                                    0.742096   
4                                    1.605504   
...                                       ...   
1616                                34.857764   
1617                                15.685304   
1618                                57.923272   
1619                                70.423856   
1620                                 7.431092   

      AREA..MM2..OF..STROMA..IN..TISSUE._HE  \
0                                122.432688   
1                                145.747888   
2                                 44.355952   
3                                 98.095856   
4                                  8.142384   
...                                     ...   
1616                             189.825556   
1617                              37.812436   
1618                              95.313388   
1619                              49.194160   
1620                              53.174212   

      AREA..MM2..OF..TUMOR..IN..TISSUE._HE  \
0                               194.239152   
1                               228.144512   
2                                71.233472   
3                               141.224432   
4                                 8.827600   
...                                    ...   
1616                            242.533340   
1617                            101.409620   
1618                            173.301296   
1619                             88.797448   
1620                             70.625564   

      AREA.PROP...EPITHELIAL..OVER..TUMOR...IN..TISSUE._HE  \
0                                                 0.369681   
1                                                 0.361160   
2                                                 0.377316   
3                                                 0.305390   
4                                                 0.077622   
...                                                    ...   
1616                                              0.217322   
1617                                              0.627132   
1618                                              0.450013   
1619                                              0.445996   
1620                                              0.247097   

      AREA.PROP...ESI_0080..OVER..TUMOR...IN..TISSUE._HE  \
0                                               0.664784   
1                                               0.737763   
2                                               0.744607   
3                                               0.788051   
4                                               0.29

In [5]:
# Normalize HIFs and define X, y
X = df.iloc[:,:607]
X_normalized = (X-X.mean())/X.std()
X_normalized

AREA..MM2..OF..EPITHELIAL..IN..TISSUE._HE  \
0                                      0.625780   
1                                      0.890326   
2                                     -0.496558   
3                                     -0.090602   
4                                     -1.150850   
...                                         ...   
1616                                   0.148690   
1617                                   0.420710   
1618                                   0.780195   
1619                                  -0.178664   
1620                                  -0.732026   

      AREA..MM2..OF..ESI_0080..IN..TISSUE._HE  \
0                                    1.320111   
1                                    2.099043   
2                                   -0.192178   
3                                    0.965621   
4                                   -1.194802   
...                                       ...   
1616                                 0.717826   
1617                                 0.146911   
1618                                 0.877285   
1619                                 0.051085   
1620                                -0.833904   

      AREA..MM2..OF..NECROSIS..IN..TISSUE._HE  \
0                                   -0.454536   
1                                   -0.378713   
2                                   -0.334060   
3                                   -0.475329   
4                                   -0.432223   
...                                       ...   
1616                                 1.227934   
1617                                 0.270728   
1618                                 2.379506   
1619                                 3.003612   
1620                                -0.141373   

      AREA..MM2..OF..STROMA..IN..TISSUE._HE  \
0                                  1.650450   
1                                  2.197757   
2                                 -0.182341   
3                                  1.079162   
4                                 -1.032426   
...                                     ...   
1616                               3.232446   
1617                              -0.335945   
1618                               1.013846   
1619                              -0.068767   
1620                               0.024661   

      AREA..MM2..OF..TUMOR..IN..TISSUE._HE  \
0                                 1.312188   
1                                 1.778738   
2                                -0.380414   
3                                 0.582686   
4                                -1.239142   
...                                    ...   
1616                              1.976733   
1617                              0.034820   
1618                              1.024075   
1619                             -0.138728   
1620                             -0.388779   

      AREA.PROP...EPITHELIAL..OVER..TUMOR...IN..TISSUE._HE  \
0                                                -0.561140   
1                                                -0.609883   
2                                                -0.517463   
3                                                -0.928909   
4                                                -2.231844   
...                                                    ...   
1616                                             -1.432699   
1617                                              0.911593   
1618                                             -0.101601   
1619                                             -0.124584   
1620                                             -1.262373   

      AREA.PROP...ESI_0080..OVER..TUMOR...IN..TISSUE._HE  \
0                                               0.228032   
1                                               0.646773   
2                                               0.686040   
3                                               0.935311   
4                                              -1.89

In [6]:
y = df.iloc[:,607]
print(np.sum(y))

769


In [7]:
# Load in clusters
clusters = pd.read_csv("{0}/data/hif_clusters/pancancer.hif.clusters.csv".format(working_dir))
print("Number of Clusters: {0}".format(len(set(clusters['x']))))
clusters


Number of Clusters: 20


Unnamed: 0  x
0    AREA (MM2) OF [EPITHELIAL] IN [TISSUE]_HE  1
1      AREA (MM2) OF [ESI_0080] IN [TISSUE]_HE  1
2      AREA (MM2) OF [NECROSIS] IN [TISSUE]_HE  2
3        AREA (MM2) OF [STROMA] IN [TISSUE]_HE  3
4         AREA (MM2) OF [TUMOR] IN [TISSUE]_HE  1
..                                         ... ..
602     TOTAL [MACROPHAGE CELLS] IN [TUMOR]_HE  1
603    TOTAL [PLASMA CELLS] IN [EPITHELIAL]_HE  1
604      TOTAL [PLASMA CELLS] IN [ESI_0080]_HE  9
605        TOTAL [PLASMA CELLS] IN [STROMA]_HE  9
606         TOTAL [PLASMA CELLS] IN [TUMOR]_HE  9

[607 rows x 2 columns]

## Define Training Process as Function

In [7]:
def train_process(X_normalized, y):
    # define nested CV parameters
    num_outer_loops = 3 # for estimating generalization error
    num_inner_loops = 5 # for hyper-parameter tuning

    # Define outer loops (A, B, and C)
    X_train_AB, X_train_C, y_train_AB, y_train_C = train_test_split(X_normalized, y, test_size=1/3, random_state=seed, stratify=y)
    X_train_A, X_train_B, y_train_A, y_train_B = train_test_split(X_train_AB, y_train_AB, test_size=1/2, random_state=seed, stratify=y_train_AB)
    
    ################
    # Outer loop 1 #
    ################
    # Define outer loop train and test
    X_train_1 = np.array(X_train_A.append(X_train_B))
    y_train_1 = np.array(y_train_A.append(y_train_B))
    # print(X_train_1.shape, y_train_1.shape)
    
    # No need for cross-validation for hyper-parameter tuning
    # Use already defined hyper-parameters
    optimal_log_reg = -3.6
    optimal_reg = np.exp(optimal_log_reg)
    # print(optimal_log_reg, optimal_reg)

    # Fit "optimal model"
    optimal_sgl = LogisticGroupLasso(groups=clusters['x'], group_reg=optimal_reg*(1/6), l1_reg=optimal_reg*(5/6), n_iter=1000, 
                             tol=1e-6, old_regularisation=False, warm_start=False, random_state=seed)
    optimal_sgl.fit(X_train_1, y_train_1)

    # Store optimal model
    optimal_sgl_1 = optimal_sgl
    
    # Store betas
    sparsity_mask = optimal_sgl.sparsity_mask_
    betas_1 = optimal_sgl.coef_[:, 1] - optimal_sgl.coef_[:, 0]
    betas_1[~sparsity_mask] = 0.0 # if not included in model, set to 0
    
    ################
    # Outer loop 2 #
    ################
    # Define outer loop train and test
    X_train_2 = np.array(X_train_A.append(X_train_C))
    y_train_2 = np.array(y_train_A.append(y_train_C))
    
    # Use already defined hyper-parameters
    optimal_log_reg = -3.6
    optimal_reg = np.exp(optimal_log_reg)
    # print(optimal_log_reg, optimal_reg)

    # Fit "optimal model"
    optimal_sgl = LogisticGroupLasso(groups=clusters['x'], group_reg=optimal_reg*(1/6), l1_reg=optimal_reg*(5/6), n_iter=1000, 
                             tol=1e-6, old_regularisation=False, warm_start=False, random_state=seed)
    optimal_sgl.fit(X_train_2, y_train_2)

    # Store optimal model
    optimal_sgl_2 = optimal_sgl
    
    # Store betas
    sparsity_mask = optimal_sgl.sparsity_mask_
    betas_2 = optimal_sgl.coef_[:, 1] - optimal_sgl.coef_[:, 0]
    betas_2[~sparsity_mask] = 0.0 # if not included in model, set to 0
    
    ################
    # Outer loop 3 #
    ################
    # Define outer loop train and test
    X_train_3 = np.array(X_train_B.append(X_train_C))
    y_train_3 = np.array(y_train_B.append(y_train_C))
    
    # Choose best regularization parameter based on CV plot
    optimal_log_reg = -3.6
    optimal_reg = np.exp(optimal_log_reg)
    # print(optimal_log_reg, optimal_reg)

    # Fit "optimal model"
    optimal_sgl = LogisticGroupLasso(groups=clusters['x'], group_reg=optimal_reg*(1/6), l1_reg=optimal_reg*(5/6), n_iter=1000, 
                             tol=1e-6, old_regularisation=False, warm_start=False, random_state=seed)
    optimal_sgl.fit(X_train_3, y_train_3)

    # Store optimal model
    optimal_sgl_3 = optimal_sgl
    
    # Store betas
    sparsity_mask = optimal_sgl.sparsity_mask_
    betas_3 = optimal_sgl.coef_[:, 1] - optimal_sgl.coef_[:, 0]
    betas_3[~sparsity_mask] = 0.0 # if not included in model, set to 0
    
    ##################
    # Ensemble betas #
    ##################
    betas_df = pd.DataFrame({
        "HIF": clusters['Unnamed: 0'],
        "Beta_1": betas_1, 
        "Beta_2": betas_2,
        "Beta_3": betas_3,
        "Cluster": clusters['x']
        }
    )
    betas_df['Beta'] = (betas_df['Beta_1'] + betas_df['Beta_2'] + betas_df['Beta_3'])/3.0
    
    return betas_df[['HIF', 'Beta']]
    

## Run Permutation Test

In [8]:
num_iterations = 5000
hif_null_distributions = {}

for hif_name in clusters['Unnamed: 0']:
    hif_null_distributions[hif_name] = []

In [9]:
# Generate N permutations of binary y vector
# Permutation = Sample WITHOUT replacement
y_permutations = []
for i in range(num_iterations):
    y_permutations.append(np.random.choice(y, size=(len(y), ), replace=False))
# y_permutations

In [10]:
# sanity check
print(np.sum(y), np.sum(y_permutations[0]), np.sum(y_permutations[1]))

769 769 769


In [ ]:
for iteration in range(num_iterations):
    y_perm = pd.DataFrame(y_permutations[iteration])
    
    # Same X, permuted Y
    betas_df = train_process(X_normalized, y_perm)
    
    # Add to null distribution samples
    for index, row in betas_df.iterrows():
        hif_null_distributions[row['HIF']].append(row['Beta'])

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it 

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

...

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expected, otherwise,try to increase the number of iterations or decreasing the tolerance.

/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_group_lasso.py:403: UserWarning:


The behaviour has changed since v1.1.1, before then, a bug in the optimisation
algorithm made it so the regularisation parameter was scaled by the largest 
eigenvalue of the covariance matrix.

To use the old behaviour, initialise the class with the keyword argument 
`old_regularisation=True`.

To supress this warning, initialise the class with the keyword argument
`supress_warning=True`


/Users/jason.wang/opt/miniconda3/lib/python3.7/site-packages/group_lasso/_fista.py:55: RuntimeWarning:

The FISTA iterations did not converge to a sufficient minimum.
You used subsampling then this is expec

In [ ]:
betas_df.sort_values(by='Beta', ascending=False)

In [ ]:
for k, v in hif_null_distributions.items():
    print(k)
    print(sorted(v))
    break